# Introduction/Business Problem

Topic - Mumbai Buyers and Tenants Choice Made Simple

Mumbai, the financial capital of India and the second most populous city in the country.When it comes to choosing a location to buy or take a house on rent,it becomes a difficult choice in Mumbai.

The buyers/tenants face difficulty in knowing the neighborhood well without visting the place. With Mumbai being known for its huge length and breadth, the report should be able to give them a snapshot of the areas they are looking out for.

The data analysis should make it simpler for the prospective buyers and tenants,to help them identify their area of choice.The report will help them in analyzing each area as to what services will be available close by.The report should list the skyscrapers in the particular area and hence the users get to know the name of the buildings,location and the prospective service providers in the neighbourhood.

In [1]:
import numpy as np
from IPython.display import display, HTML
from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
#import folium
# import k-means from clustering stage
from sklearn.cluster import KMeans
!pip install folium
import folium

     |████████████████████████████████| 94 kB 4.5 MB/s  eta 0:00:01


# Data Section
The data is imported from a csv file which lists all the property data which is available for lease/sale in Mumbai.


In [2]:
# The code was removed by Watson Studio for sharing.

area  bathroom_num  bedroom_num    city  \
0       350.0           2.0            1  Mumbai   
1       652.0           2.0            1  Mumbai   
2       635.0           2.0            1  Mumbai   
3       540.0           2.0            1  Mumbai   
4       625.0           1.0            1  Mumbai   
...       ...           ...          ...     ...   
34343   700.0           2.0            1  Mumbai   
34344   750.0           2.0            1  Mumbai   
34345   700.0           2.0            1  Mumbai   
34346   750.0           2.0            1  Mumbai   
34347  1100.0           2.0            2  Mumbai   

                                                    desc            dev_name  \
0      2 Bath,Unfurnished,East facing The project has...                 NaN   
1      2 Bath,Semi-Furnished,East facing A 1BHK apart...         Veena Group   
2      2 Bath,Semi-Furnished,4 floor,West facing A be...       Agarwal Group   
3      2 Bath,Semi-Furnished,East facing Essential Se...                 NaN   
4      1 Bath,Furnished,2 floor,North facing 24 hours...    Millennium Group   
...                                                  ...                 ...   
34343  2 Bath,Semi-Furnished,5 floor,North facing 1 B...  Evershine Builders   
34344  2 Bath,Semi-Furnished,7 floor,West facing 1 BH...        Poonam Group   
34345  2 Bath,Semi-Furnished,4 floor,North facing 1 B...        Vinay Unique   
34346  2 Bath,Semi-Furnished,4 floor 1 BHK, Multistor...        Vinay Unique   
34347  2 Bath,Unfurnished,7 floor,South -West facing ...                 NaN   

       floor_count  floor_num      furnishing        id  ...  \
0              NaN        NaN     Unfurnished  45349857  ...   
1              NaN        NaN  Semi-Furnished  45960973  ...   
2              7.0        4.0  Semi-Furnished  46688849  ...   
3              NaN        NaN  Semi-Furnished  44696119  ...   
4              7.0        2.0       Furnished  46742851  ...   
...            ...        ...             ...       ...  ...   
34343          7.0        5.0  Semi-Furnished  46601107  ...   
34344         12.0        7.0  Semi-Furnished  46601343  ...   
34345         12.0        4.0  Semi-Furnished  46600981  ...   
34346         12.0        4.0  Semi-Furnished  46600943  ...   
34347         10.0        7.0     Unfurnished  18660587  ...   

               longitude   post_date       poster_name    price  \
0      72.82588195800781  2020-01-11     Saurabh Patil     9000   
1            72.83359245  2020-01-11    Gorakh  Chavan     8060   
2            72.80161155  2019-12-13      Lokesh Joshi     8000   
3      72.83600616455078  2020-01-13    Sajith  Thomas     8000   
4      72.85016654221559  2019-12-17  Charmaine  Gomez     9000   
...                  ...         ...               ...      ...   
34343        72.80061282  2019-12-09    Rambahad Singh     7000   
34344                0.0  2019-12-09    Rambahad Singh     6500   
34345         72.7955643  2019-12-09    Rambahad Singh     6500   
34346         72.7955643  2019-12-09    Rambahad Singh     6500   
34347                0.0  2019-12-30     Rishi  Dusija  1200000   

                    project  \
0                       NaN   
1             Veena Dynasty   
2         Agarwal Lifestyle   
3                       NaN   
4            Mittal Enclave   
...                     ...   
34343       Evershine Homes   
34344        Poonam Heights   
34345  Vinay Unique Heights   
34346  Vinay Unique Heights   
34347                   NaN   

                                                   title  trans  \
0                 1 BHK Apartment for Rent in Malad West   Rent   
1       1 BHK Apartment for Rent in Veena Dynasty, Vasai   Rent   
2      1 BHK Apartment for Rent in Agarwal Lifestyle,...   Rent   
3                 1 BHK Apartment for Rent in Vasai East   Rent   
4      1 BHK Apartment for Rent in Mittal Enclave, Na...   Rent   
...                                                  ...    ...   
34343  

# Cleaning the data

The data consists of 34348 rows and 23 columns.As the data is huge we will be cleaning the data so that it becomes easir to understand for sample study.
The following columns will be removed:
1)city
2)desc
3)dev_name
4)floor_count
5)floor_num
6)id
7)id_string
8)post_date
9)poster_name
10)title
11)trans
12)type
13)url

The data which has Nan value will be removed.The duplicate records will also be deleted.
We get 19899 rows.


In [3]:
df_data1 = df_data.drop(['city','desc','dev_name','floor_count', 'floor_num', 'id', 'id_string','post_date', 'poster_name',
       'title', 'trans', 'type', 'url'],axis='columns')


#df_data1 = df_data1.drop(df_data[df_data.latitude=='0.0'])
df_data1.shape
df_data1 =df_data1[df_data1['latitude'] !=0.0]
df_data1 =df_data1[df_data1['longitude'] !=0.0]
df_data1 =df_data1[df_data1['locality'] !='']
df_data1.loc[(df_data1!=0.0).any(axis=1)]
indexNames = df_data1[(df_data1['latitude'] =='0.0') & (df_data1['longitude'] == '0.0')].index
df_data1.drop(indexNames , inplace=True)
df_data1.drop_duplicates()
df_data1.reset_index(drop=True, inplace=True)
df_data1['user_type'].unique()
df_data1.isnull().sum()
df_ready = df_data1.dropna()
df_ready.isnull().sum()
df_ready

area  bathroom_num  bedroom_num      furnishing          latitude  \
1      652.0           2.0            1  Semi-Furnished       19.41070368   
2      635.0           2.0            1  Semi-Furnished       19.46703238   
4      625.0           1.0            1       Furnished  19.3602150985917   
5      630.0           2.0            1     Unfurnished         19.470536   
6      690.0           2.0            1       Furnished       19.46825836   
...      ...           ...          ...             ...               ...   
24795  700.0           2.0            1  Semi-Furnished       19.46778327   
24796  680.0           2.0            1     Unfurnished         19.471987   
24797  700.0           2.0            1  Semi-Furnished       19.46825836   
24798  700.0           2.0            1  Semi-Furnished         19.470357   
24799  750.0           2.0            1  Semi-Furnished         19.470357   

           locality          longitude  price               project user_type  
1             Vasai        72.83359245   8060         Veena Dynasty     Agent  
2             Virar        72.80161155   8000     Agarwal Lifestyle     Agent  
4      Naigaon East  72.85016654221559   9000        Mittal Enclave     Owner  
5        Virar West          72.808309   8000      Poonam Park View     Agent  
6             Virar        72.80061282   8500       Evershine Homes     Agent  
...             ...                ...    ...                   ...       ...  
24795         Virar        72.79647106   6500        Cosmos Regency     Agent  
24796    Virar West          72.800387   6500       Ekta Parksville     Agent  
24797         Virar        72.80061282   7000       Evershine Homes     Agent  
24798         Virar         72.7955643   6500  Vinay Unique Heights     Agent  
24799         Virar         72.7955643   6500  Vinay Unique Heights     Agent  

[17301 rows x 10 columns]

Drop locations that have less than 10 occurences

# Data contd.

Further the location count is done,the locations which has less than 50 occurences are taken into account.The subset dataframe of locality,longitude,longitude is created.This data will be passed to Fouresquare API.Only 500 such records are sent to Fouresquare API as it only allows 500 calls a day.
The most common venues will be reported for a particular location which will give the user a clear picture about the most common service providers corresponding to each building and area

In [4]:
location = df_ready['locality'].value_counts()
#print(location)
print(location.values.sum())
len(location[location<=50])
location_stats_less_than_1000 = location[location<=50]
#print(location_stats_less_than_500)
df = location_stats_less_than_1000.sort_index().rename_axis('l').reset_index(name='count')
print(df['l'].value_counts())
df_ready = df_ready[df_ready['locality'].isin(df['l'])]
df_ready.reset_index(drop=True, inplace=True)
location = df_ready['locality'].value_counts()
df_location=df_ready.loc[:, ['locality','latitude','longitude']]
df_location.drop_duplicates()
df_location.reset_index(drop=True, inplace=True)
#df_location1 = df_location['locality'].unique()
#print(df_location1.size)
df_location = df_location.head(500)
#df_final = df_ready[df_ready['locality'].isin(df_location['locality'])]
#print(df_location)
#df_ready.drop(df_[ready[df_ready.locality.isin(df['l']])].index.tolist())
#df_final

17301
Hanuman Tekdi - Goregaon East     1
Jogeshwari East                   1
Rajawadi                          1
Samta Nagar                       1
Nalasopara West                   1
                                 ..
Mandapeshwar                      1
Panchsheel Nagar                  1
Worli Naka Acharaya Atre Chowk    1
Holy Family Hospital              1
Vishveshwar Nagar                 1
Name: l, Length: 415, dtype: int64


In [5]:
CLIENT_ID = 'WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI' # your Foursquare ID
CLIENT_SECRET = 'CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WPHQ4ZFRPXYO2TFLNZRM2BQ1WLTXT40FAQKZ4BYO1USMQNUI
CLIENT_SECRET:CFJYBM04XN02NANX14R5XZKNKFUJLPXIG2S23BG4ZKLISRWG


In [6]:
def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
       # print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        #print(url)  
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

# Methodology

Four Square API is used to explore the venues for the residential projects locations passed alongwith latitude and longitude.
The most common 10 venues for a particular location are grouped by neighbourhood.
then further the data recieved from FourSquare API is merged with the property data based on locality.

In [7]:
 mumbai_venues = getNearbyVenues(names=df_location['locality'],
                                   latitudes=df_location['latitude'],
                                   longitudes=df_location['longitude']
                                  )
mumbai_venues.groupby('Neighborhood').count()

KeyError: 'groups'

In [ ]:
# one hot encoding
mumbai_onehot = pd.get_dummies(mumbai_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
mumbai_onehot['Neighborhood'] = mumbai_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [mumbai_onehot.columns[-1]] + list(mumbai_onehot.columns[:-1])
mumbai_onehot = mumbai_onehot[fixed_columns]

mumbai_onehot.head(10)
mumbai_onehot.shape
mumbai_grouped = mumbai_onehot.groupby('Neighborhood').mean().reset_index()
mumbai_grouped.shape

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [10]:
num_top_venues = 10

for hood in mumbai_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = mumbai_grouped[mumbai_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Akurli Nagar----
                  venue  freq
0     Indian Restaurant  0.10
1  Fast Food Restaurant  0.06
2           Coffee Shop  0.05
3         Shopping Mall  0.04
4           Pizza Place  0.04
5        Ice Cream Shop  0.04
6            Donut Shop  0.04
7                  Café  0.03
8    Seafood Restaurant  0.03
9        Clothing Store  0.03


----Amar Nagar----
                  venue  freq
0     Indian Restaurant  0.17
1  Fast Food Restaurant  0.07
2                  Café  0.06
3        Ice Cream Shop  0.06
4           Snack Place  0.05
5           Pizza Place  0.05
6          Dessert Shop  0.03
7            Restaurant  0.03
8    Italian Restaurant  0.03
9              Mountain  0.02


----Andheri----
                  venue  freq
0     Indian Restaurant  0.11
1                 Hotel  0.09
2        Ice Cream Shop  0.06
3    Italian Restaurant  0.06
4                Lounge  0.05
5           Coffee Shop  0.04
6               Brewery  0.03
7    Chinese Restaurant  0.03
8         

In [11]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [12]:
from IPython.display import display, HTML
def display_print(df2):
    return display( HTML( df2.to_html().replace("\\n","<br>") ) )

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [13]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = mumbai_grouped['Neighborhood']

for ind in np.arange(mumbai_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(mumbai_grouped.iloc[ind, :], num_top_venues)

print(display_print(neighborhoods_venues_sorted))

None


# Methodology Contd.
Run k-means to cluster the neighborhood into 5 clusters.
Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [14]:
# set number of clusters
kclusters = 5

mumbai_grouped_clustering = mumbai_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mumbai_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 0, 3, 4, 2, 3, 1, 2, 1, 1], dtype=int32)

In [15]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
df_final = df_ready[df_ready['locality'].isin(df_location['locality'])]
mumbai_merged = df_final#df_ready

# merge manhattan_grouped with toronto_data to add latitude/longitude for each neighborhood
mumbai_merged = mumbai_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on=['locality'])
#mumbai_merged = mumbai_merged.drop(mumbai_merged.columns[[5,6]], axis=1)
#mumbai_merged.reset_index(drop=True, inplace=True)
print(display_print(mumbai_merged))
mumbai_merged.shape

None


(2012, 21)

# Result
Finally, let's visualize the resulting clusters.

In [16]:
from geopy.geocoders import Nominatim
address = 'Mumbai,IN'

geolocator = Nominatim(user_agent="mumbai_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mumbai City are {}, {}.'.format(latitude, longitude))
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(mumbai_merged['latitude'], mumbai_merged['longitude'], mumbai_merged['locality'], mumbai_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[np.isnan(cluster)-1],
        fill=True,
        fill_color=rainbow[np.isnan(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

The geograpical coordinate of Mumbai City are 19.0759899, 72.8773928.


#Cluster 1

In [18]:
mumbai_merged.loc[mumbai_merged['Cluster Labels'] == 0, mumbai_merged.columns[[1] + list(range(5, mumbai_merged.shape[1]))]]

bathroom_num        locality         longitude  price  \
0              2.0           Vasai       72.83359245   8060   
1              1.0      Vasai West       72.81293356  10000   
2              1.0      Vasai East         72.838665   8500   
5              1.0      Vasai East       72.82404898   8000   
6              1.0  Bhayandar East        72.8507483   9000   
...            ...             ...               ...    ...   
2511           2.0           Vasai         72.831056   6000   
2518           2.0      Vasai East       72.80594237   6000   
2903           1.0           Vasai         72.838665   7500   
2905           1.0           Vasai         72.838665   7500   
2907           1.0      Dongarpada  72.8132122351175   6500   

                        project user_type  Cluster Labels  \
0                 Veena Dynasty     Agent               0   
1     Agarwal and Doshi Complex     Agent               0   
2                Evershine City     Agent               0   
5                      Samarpan     Owner               0   
6                     Sai Kiran     Owner               0   
...                         ...       ...             ...   
2511           Rashmi Lake View     Agent               0   
2518            Poonam Imperial     Agent               0   
2903             Evershine City     Owner               0   
2905             Evershine City     Owner               0   
2907       Vinay Unique Gardens     Agent               0   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pizza Place     Indian Restaurant            Restaurant   
1        Indian Restaurant            Restaurant  Fast Food Restaurant   
2     Fast Food Restaurant           Pizza Place     Indian Restaurant   
5     Fast Food Restaurant           Pizza Place     Indian Restaurant   
6        Indian Restaurant  Fast Food Restaurant           Pizza Place   
...                    ...                   ...                   ...   
2511           Pizza Place     Indian Restaurant            Restaurant   
2518  Fast Food Restaurant           Pizza Place     Indian Restaurant   
2903           Pizza Place     Indian Restaurant            Restaurant   
2905           Pizza Place     Indian Restaurant            Restaurant   
2907     Indian Restaurant  Fast Food Restaurant            Restaurant   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                Multiplex           Bus Station                   Gym   
1              Coffee Shop         Train Station    Seafood Restaurant   
2                Multiplex            Restaurant           Bus Station   
5                Multiplex            Restaurant           Bus Station   
6               Restaurant             Multiplex        Ice Cream Shop   
...                    ...                   ...                   ...   
2511             Multiplex           Bus Station                   Gym   
2518             Multiplex            Restaurant           Bus Station   
2903             Multiplex           Bus Station                   Gym   
2905             Multiplex           Bus Station                   Gym   
2907           Pizza Place                   Gym        Ice Cream Shop   

     7th Most Common Venue 8th Most Common Venue  \
0     Fast Food Restaurant        Ice Cream Shop   
1                      Gym           Pizza Place   
2                      Gym        Ice Cream Shop   
5                      Gym        Ice Cream Shop   
6            Train Station           Coffee Shop   
...                    ...                   ...   
2511  Fast Food Restaurant        Ice Cream Shop   
2518                   Gym        Ice Cream Shop   
2903  Fast Food Restaurant        Ice Cream Shop   
2905  Fast Food Restaurant        Ice Cream Shop   
2907           Coffee Shop            Food Court   

               9th Most Common Venue 10th Most Common Venue  
0                              Dhaba         Cricke

#Cluster 2

In [19]:
mumbai_merged.loc[mumbai_merged['Cluster Labels'] == 1, mumbai_merged.columns[[1] + list(range(5, mumbai_merged.shape[1]))]]

bathroom_num                        locality          longitude   price  \
44             1.0                     Elphinstone  72.83419650675529   10333   
127            6.0                      Worli Hill  72.83124868364351  180000   
134            4.0                  Mumbai Central  72.82439079999999  180000   
135            4.0                        Bhoiwada   72.8505157603601  170000   
136            4.0                    Shivaji Park   72.8380752064758  175000   
...            ...                             ...                ...     ...   
2889           3.0                  Nepeansea Road         72.8008476  475000   
2890           4.0  Worli Naka Acharaya Atre Chowk   72.8212818559477  400000   
2892           3.0                  Gamadia Colony   72.8139579750458  400000   
2894           3.0                          Tardeo   72.8139579750458  450000   
2896           3.0               Bandra Band Stand         72.8185814  675000   

                project user_type  Cluster Labels 1st Most Common Venue  \
44         Royal Palace     Owner               1     Indian Restaurant   
127      Lodha The Park     Agent               1     Indian Restaurant   
134   DB Orchid Enclave     Agent               1     Indian Restaurant   
135        Crescent Bay     Agent               1     Indian Restaurant   
136     Amber Kutir CHS     Agent               1     Indian Restaurant   
...                 ...       ...             ...                   ...   
2889         Orbit Arya     Agent               1     Indian Restaurant   
2890     Indiabulls Blu     Agent               1     Indian Restaurant   
2892    Imperial Towers     Agent               1     Indian Restaurant   
2894    Imperial Towers     Agent               1     Indian Restaurant   
2896    Jivesh Terraces     Agent               1     Indian Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
44                    Café            Restaurant                Lounge   
127                   Café                 Hotel            Restaurant   
134                  Hotel            Restaurant        Scenic Lookout   
135                   Café        Ice Cream Shop            Restaurant   
136                   Café    Seafood Restaurant         Deli / Bodega   
...                    ...                   ...                   ...   
2889            Restaurant                 Hotel        Ice Cream Shop   
2890            Restaurant                 Hotel                  Café   
2892            Restaurant        Ice Cream Shop                  Café   
2894                 Hotel            Restaurant        Ice Cream Shop   
2896                  Café                Bakery          Dessert Shop   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
44               Juice Bar        Scenic Lookout                 Hotel   
127         Ice Cream Shop        Scenic Lookout             Juice Bar   
134                   Café        Ice Cream Shop           Pizza Place   
135                    Bar           Snack Place                 Hotel   
136                 Bakery        Ice Cream Shop      Asian Restaurant   
...                    ...                   ...                   ...   
2889                  Café          Dessert Shop                   Bar   
2890             Juice Bar                   Bar        Scenic Lookout   
2892          Dessert Shop                 Hotel        Scenic Lookout   
2894        Scenic Lookout                  Café          Dessert Shop   
2896        Ice Cream Shop    Seafood Restaurant                Lounge   

     8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
44                  Bakery                   Bar              Deli / Bodega  
127                    Bar                Bakery   Maharashtrian Restaurant  
134                    Bar          Dessert Shop             Cricket Ground  
135              Multiplex           Coffe

#Cluster 3

In [20]:
mumbai_merged.loc[mumbai_merged['Cluster Labels'] == 2, mumbai_merged.columns[[1] + list(range(5, mumbai_merged.shape[1]))]]

bathroom_num                    locality          longitude   price  \
33             4.0                        Madh         72.7935571   60000   
34             4.0          Upper Govind Nagar         72.8514162   60000   
35             3.0                        Madh            72.7957   75000   
40             2.0  Ashok Nagar Western Mumbai  72.83850600000001   12500   
64             4.0      CAMA Industrial Estate         72.8540607  100000   
...            ...                         ...                ...     ...   
2853           3.0                        Juhu        72.83417232  300000   
2857           4.0               Gulmohar Road        72.83417232  290000   
2862           3.0                        Juhu        72.83417232  275100   
2864           3.0                        Juhu  72.82523690000001  289000   
2867           3.0                        Juhu        72.83417232  300000   

                     project user_type  Cluster Labels 1st Most Common Venue  \
33            Raheja Exotica     Agent               2                 Beach   
34          Moksh Apartments     Agent               2     Indian Restaurant   
35    Raheja Exotica Sorento     Agent               2                 Beach   
40        Morarji Mill Mhada     Agent               2     Indian Restaurant   
64            Lodha Fiorenza     Agent               2     Indian Restaurant   
...                      ...       ...             ...                   ...   
2853     Kalpataru Solitaire     Agent               2     Indian Restaurant   
2857     Kalpataru Solitaire     Agent               2                 Hotel   
2862     Kalpataru Solitaire     Agent               2     Indian Restaurant   
2864             Janki Kutir     Agent               2     Indian Restaurant   
2867     Kalpataru Solitaire     Agent               2     Indian Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
33       Indian Restaurant                Bakery                  Café   
34             Coffee Shop  Fast Food Restaurant             Multiplex   
35       Indian Restaurant                Bakery                  Café   
40             Coffee Shop            Donut Shop  Fast Food Restaurant   
64             Coffee Shop    Chinese Restaurant           Pizza Place   
...                    ...                   ...                   ...   
2853                  Café                 Hotel           Coffee Shop   
2857     Indian Restaurant                  Café                   Pub   
2862                  Café                 Hotel           Coffee Shop   
2864                  Café                 Hotel           Coffee Shop   
2867                  Café                 Hotel           Coffee Shop   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
33                     Pub                   Bar           Pizza Place   
34      Chinese Restaurant                   Pub        Clothing Store   
35                     Pub                   Bar           Pizza Place   
40      Chinese Restaurant             Multiplex        Clothing Store   
64               Multiplex                Bakery  Fast Food Restaurant   
...                    ...                   ...                   ...   
2853                   Pub        Ice Cream Shop                   Bar   
2857           Coffee Shop             Juice Bar        Ice Cream Shop   
2862                   Pub        Ice Cream Shop                   Bar   
2864                   Pub        Ice Cream Shop                   Bar   
2867                   Pub        Ice Cream Shop                   Bar   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
33           Boat or Ferry    Chinese Restaurant            Coffee Shop  
34                  Lounge         Shopping Mall     Italian Restaurant  
35           Boat or Ferry    Chinese Restaurant            Coffee Shop  
40           Shopping Mall                   B

In [21]:
mumbai_merged.loc[mumbai_merged['Cluster Labels'] == 3, mumbai_merged.columns[[1] + list(range(5, mumbai_merged.shape[1]))]]

bathroom_num                   locality    longitude   price  \
26             2.0  Bhandup Industrial Estate    72.936521   41000   
42             1.0            Pratiksha Nagar     72.87535   11000   
49             1.0            Pratiksha Nagar     72.87535   11000   
52             1.0            Pratiksha Nagar     72.87535   11000   
53             1.0            Pratiksha Nagar     72.87535   11000   
...            ...                        ...          ...     ...   
2723           3.0                       Sion   72.8663429  155000   
2726           3.0                       Sion   72.8663429  155000   
2750           3.0    Panchkutir Ganesh Nagar   72.9116964  150000   
2752           3.0    Panchkutir Ganesh Nagar  72.90883363  135000   
2797           3.0    Panchkutir Ganesh Nagar  72.91224898  160000   

                               project user_type  Cluster Labels  \
26                      Dreams Complex     Agent               3   
42          Mhada Pratiksha Nagar Sion     Owner               3   
49          Mhada Pratiksha Nagar Sion     Owner               3   
52          Mhada Pratiksha Nagar Sion     Owner               3   
53          Mhada Pratiksha Nagar Sion     Owner               3   
...                                ...       ...             ...   
2723                    Raheja Regency     Agent               3   
2726                    Raheja Regency     Agent               3   
2750               Glen Dale Apartment     Agent               3   
2752  Verona Co op Housing Society Ltd     Agent               3   
2797               Hiranandani Gardens     Agent               3   

     1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
26       Indian Restaurant                  Café            Restaurant   
42       Indian Restaurant          Dessert Shop                   Bar   
49       Indian Restaurant          Dessert Shop                   Bar   
52       Indian Restaurant          Dessert Shop                   Bar   
53       Indian Restaurant          Dessert Shop                   Bar   
...                    ...                   ...                   ...   
2723     Indian Restaurant                   Bar          Dessert Shop   
2726     Indian Restaurant                   Bar          Dessert Shop   
2750     Indian Restaurant           Coffee Shop                 Hotel   
2752     Indian Restaurant           Coffee Shop                 Hotel   
2797     Indian Restaurant           Coffee Shop                 Hotel   

     4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
26                  Lounge                   Pub        Ice Cream Shop   
42          Ice Cream Shop                Lounge                  Café   
49          Ice Cream Shop                Lounge                  Café   
52          Ice Cream Shop                Lounge                  Café   
53          Ice Cream Shop                Lounge                  Café   
...                    ...                   ...                   ...   
2723         Deli / Bodega        Ice Cream Shop           Snack Place   
2726         Deli / Bodega        Ice Cream Shop           Snack Place   
2750    Italian Restaurant                Lounge        Ice Cream Shop   
2752    Italian Restaurant                Lounge        Ice Cream Shop   
2797    Italian Restaurant                Lounge        Ice Cream Shop   

     7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
26             Snack Place    Italian Restaurant                   Bar   
42      Italian Restaurant           Snack Place                 Hotel   
49      Italian Restaurant           Snack Place                 Hotel   
52      Italian Restaurant           Snack Place                 Hotel   
53      Italian Restaurant           Snack Place                 Hotel   
...                    ...                   ...                   ...   
2723                Bakery    Italian Restaurant    

In [22]:
mumbai_merged.loc[mumbai_merged['Cluster Labels'] == 4, mumbai_merged.columns[[1] + list(range(5, mumbai_merged.shape[1]))]]

bathroom_num          locality         longitude   price  \
3              1.0            Kalyan        73.1197768   10000   
4              1.0            Kalyan        73.1197768    9500   
27             3.0   Charkop Village       72.81912281   36000   
28             2.0         Devi Pada  72.8644433333333   45000   
29             2.0   Jankalyan Nagar       72.81670496   42000   
...            ...               ...               ...     ...   
2650           3.0  Sai Baba Complex       72.86478709  110000   
2674           3.0  Sai Baba Complex       72.86478709  110000   
2705           3.0         Yeshodham       72.86478709  130000   
2708           3.0         Yeshodham       72.86478709  150000   
2906           1.0      Bhandup East        72.9429424    6500   

                 project user_type  Cluster Labels 1st Most Common Venue  \
3            Raunak City     Owner               4  Fast Food Restaurant   
4            Raunak City     Owner               4  Fast Food Restaurant   
27    Rustomjee Meridian     Agent               4     Indian Restaurant   
28              Ambrosia     Agent               4     Indian Restaurant   
29        Marina Enclave     Agent               4     Indian Restaurant   
...                  ...       ...             ...                   ...   
2650    Oberoi Exquisite     Agent               4  Fast Food Restaurant   
2674    Oberoi Exquisite     Agent               4  Fast Food Restaurant   
2705    Oberoi Exquisite     Agent               4     Indian Restaurant   
2708    Oberoi Exquisite     Agent               4     Indian Restaurant   
2906           Hema Park     Owner               4     Indian Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3                     Café           Pizza Place     Indian Restaurant   
4                     Café           Pizza Place     Indian Restaurant   
27    Fast Food Restaurant           Coffee Shop                  Café   
28    Fast Food Restaurant            Restaurant    Chinese Restaurant   
29    Fast Food Restaurant           Coffee Shop                  Café   
...                    ...                   ...                   ...   
2650    Chinese Restaurant     Indian Restaurant           Coffee Shop   
2674    Chinese Restaurant     Indian Restaurant           Coffee Shop   
2705                   Bar  Fast Food Restaurant           Coffee Shop   
2708                   Bar  Fast Food Restaurant           Coffee Shop   
2906                  Café  Fast Food Restaurant           Pizza Place   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3               Hookah Bar        Ice Cream Shop                Garden   
4               Hookah Bar        Ice Cream Shop                Garden   
27              Restaurant        Ice Cream Shop    Chinese Restaurant   
28          Ice Cream Shop                  Café           Coffee Shop   
29                     Pub        Ice Cream Shop                   Gym   
...                    ...                   ...                   ...   
2650             Multiplex                   Bar        Clothing Store   
2674             Multiplex                   Bar        Clothing Store   
2705    Chinese Restaurant             Multiplex    Italian Restaurant   
2708    Chinese Restaurant             Multiplex    Italian Restaurant   
2906           Snack Place        Ice Cream Shop             Multiplex   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3                Juice Bar    Mexican Restaurant             Playground  
4                Juice Bar    Mexican Restaurant             Playground  
27                     Pub                 Beach                    Gym  
28                  Lounge           Pizza Place             Food Truck  
29                   Beach             Multiplex     Chinese Restaurant  
...                    ...                   ...                    ...  
2650